### Search
 
We'll use [Tavily Search](https://python.langchain.com/docs/integrations/tools/tavily_search) for web search.

In [36]:
import os

os.environ["TAVILY_API_KEY"] = "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"

### Tracing

Optionally, use [LangSmith](https://docs.smith.langchain.com/) for tracing (shown at bottom)

In [37]:
# os.environ["LANGCHAIN_TRACING_V2"] = "true"
# os.environ["LANGCHAIN_ENDPOINT"] = "https://api.smith.langchain.com"
# os.environ["LANGCHAIN_API_KEY"] = "<your-api-key>"

## Configuration

Decide to run locally and select LLM to use with Ollama.

In [38]:
run_local = "Yes"
local_llm = "llama2-13b"

In [39]:
# !pip install langchain_nomic

## Index

Let's index 3 blog posts.

In [2]:
# Download PDF file
import os
import requests
import fitz # (pymupdf, found this is better than pypdf for our use case, note: licence is AGPL-3.0, keep that in mind if you want to use any code commercially)
from tqdm.auto import tqdm
# Get PDF document
pdf_path = ""

# Download PDF if it doesn't already exist
if not os.path.exists(pdf_path):
  print("File doesn't exist, downloading...")

  # The URL of the PDF you want to download
  url = "https://pressbooks.oer.hawaii.edu/humannutrition2/open/download?type=pdf"

  # The local filename to save the downloaded file
  filename = pdf_path

  # Send a GET request to the URL
  response = requests.get(url)

  # Check if the request was successful
  if response.status_code == 200:
      # Open a file in binary write mode and save the content to it
      with open(filename, "wb") as file:
          file.write(response.content)
      print(f"The file has been downloaded and saved as {filename}")
  else:
      print(f"Failed to download the file. Status code: {response.status_code}")
else:
  print(f"File {pdf_path} exists.")

In [41]:
# Requires !pip install PyMuPDF, see: https://github.com/pymupdf/pymupdf
import fitz # (pymupdf, found this is better than pypdf for our use case, note: licence is AGPL-3.0, keep that in mind if you want to use any code commercially)
from tqdm.auto import tqdm # for progress bars, requires !pip install tqdm 

def text_formatter(text: str) -> str:
    """Performs minor formatting on text."""
    cleaned_text = text.replace("\n", " ").strip() # note: this might be different for each doc (best to experiment)

    # Other potential text formatting functions can go here
    return cleaned_text

# Open PDF and get lines/pages
# Note: this only focuses on text, rather than images/figures etc
def open_and_read_pdf(pdf_path: str) -> list[dict]:
    """
    Opens a PDF file, reads its text content page by page, and collects statistics.

    Parameters:
        pdf_path (str): The file path to the PDF document to be opened and read.

    Returns:
        list[dict]: A list of dictionaries, each containing the page number
        (adjusted), character count, word count, sentence count, token count, and the extracted text
        for each page.
    """
    doc = fitz.open(pdf_path)  # open a document
    pages_and_texts = ""
    for page_number, page in tqdm(enumerate(doc)):  # iterate the document pages
        text = page.get_text()  # get plain text encoded as UTF-8
        text = text_formatter(text)
        pages_and_texts+=text
        # pages_and_texts.append({"page_number": page_number - 41,  # adjust page numbers since our PDF starts on page 42
        #                         "page_char_count": len(text),
        #                         "page_word_count": len(text.split(" ")),
        #                         "page_sentence_count_raw": len(text.split(". ")),
        #                         "page_token_count": len(text) / 4,  # 1 token = ~4 chars, see: https://help.openai.com/en/articles/4936856-what-are-tokens-and-how-to-count-them
        #                         "text": text})
    return pages_and_texts

pages_and_texts = open_and_read_pdf(pdf_path=pdf_path)
pages_and_texts[:100]

In [42]:
# !pip install fastembed

In [43]:
from langchain.text_splitter import RecursiveCharacterTextSplitter,CharacterTextSplitter
from langchain_community.document_loaders import WebBaseLoader
from langchain_community.vectorstores import Chroma
from langchain_mistralai import MistralAIEmbeddings
# from langchain_nomic.embeddings import NomicEmbeddings
from langchain_community.embeddings import OllamaEmbeddings
# ollama_emb = 
# Load
from langchain_community.embeddings.fastembed import FastEmbedEmbeddings

# # Split
# text_splitter = RecursiveCharacterTextSplitter.from_tiktoken_encoder(
#     chunk_size=500, chunk_overlap=100
# )

text_splitter = CharacterTextSplitter(
    chunk_size=1000,
    chunk_overlap=200,
    separator="\n"
)


all_splits = text_splitter.create_documents(pages_and_texts)

# Embed and index
if run_local == "Yes":
    embedding = FastEmbedEmbeddings(model_name="BAAI/bge-base-en-v1.5",device="cuda")

else:
    embedding = MistralAIEmbeddings(mistral_api_key=mistral_api_key)

# Index
vectorstore = Chroma.from_documents(
    documents=all_splits,
    collection_name="rag-chroma",
    embedding=embedding,
)
retriever = vectorstore.as_retriever()

In [44]:
import fitz  # PyMuPDF
def text_formatter(text: str) -> str:
    """Performs minor formatting on text."""
    cleaned_text = text.replace("\n", " ").strip() # note: this might be different for each doc (best to experiment)

    # Other potential text formatting functions can go here
    return cleaned_text
def extract_text_from_pdf(pdf_path):
    document = fitz.open(pdf_path)
    pages_and_texts = []
    for page_num in range(len(document)):
        page = document.load_page(page_num)
        text = page.get_text("text")
        text = text_formatter(text)
        pages_and_texts.append(text)
    return pages_and_texts




In [46]:
pages_and_texts = basic+surgery

In [47]:
from langchain.text_splitter import RecursiveCharacterTextSplitter, CharacterTextSplitter
from langchain_community.document_loaders import WebBaseLoader
from langchain_community.vectorstores import Chroma
from sentence_transformers import SentenceTransformer
import torch

# Define your text splitter
text_splitter = CharacterTextSplitter(
    chunk_size=1000,
    chunk_overlap=200,
    separator=" "
)

# Assuming 'pages_and_texts' is your list of documents' text
all_splits = text_splitter.create_documents(pages_and_texts)



In [49]:
# !pip install langchain_openai

In [1]:
from langchain_community.embeddings.sentence_transformer import (
    SentenceTransformerEmbeddings,
)

if run_local == "Yes":
    embedding = SentenceTransformerEmbeddings(model_name="BAAI/bge-base-en-v1.5")
#     from langchain_openai import OpenAIEmbeddings

#     embedding = OpenAIEmbeddings(api_key="sk-proj-KQ4DlWOH3c1mSlTGHXbqT3BlbkFJ3TxJ8nsKKJyk98rFXx1x")
else:
    # Handle the case when not running locally
    embedding = MistralAIEmbeddings(mistral_api_key=mistral_api_key)



In [51]:
all_splits[156]

Document(page_content='CHAPTER 2 Diagnostic tests and their interpretation 54 Automated perimetry: performance and interpretation (2) Interpretation of Humphrey perimetry (cont.) Table 2.4 Global indices (a summary of the results as a single number used to monitor change) Mean deviation (MD) A measure of overall ﬁ eld loss. Pattern standard deviation (PSD) Measure of focal loss or variability within the ﬁ eld, taking into account any generalized depression. An increased PSD is more indicative of glaucomatous ﬁ eld loss than MD. Short-term ﬂ uctuation (SF) An indication of the consistency of responses. It is assessed by measuring threshold twice at 10 preselected points and calculated on the difference between the ﬁ rst and second measurements. Corrected pattern standard deviation (CPSD) A measure of variability within the ﬁ eld after correcting for SF (intratest variability). Table 2.3 Typical graphical results from automated perimetry (Fig. 2.2) Gray scale Decreasing sensitivity is re

In [52]:
from tqdm.notebook import tqdm

# Embed the documents with progress tracking
embedded_docs = []
# for doc in tqdm(all_splits, desc="Embedding Documents"):
#     embedded_docs.append(embedding.embed_documents([doc.page_content])[0])

    # # Embed and index
# if run_local == "Yes":
#     embedding = FastEmbedEmbeddings(model_name="BAAI/bge-base-en-v1.5",device="cuda")

# else:
#     embedding = MistralAIEmbeddings(mistral_api_key=mistral_api_key)

# # Index
# vectorstore = Chroma.from_documents(
#     documents=all_splits,
#     collection_name="rag-chroma",
#     embedding=embedding,
# )
# retriever = vectorstore.as_retriever()
    
    
# Store in Chroma vector store
vectorstore = Chroma.from_documents(
    embedding=embedding,
    documents=all_splits,
    collection_name="rag-chroma"
)

# Use the vector store as a retriever


In [53]:
# # Embed the documents
# embedded_docs = embedding.embed_documents([doc.page_content for doc in all_splits])

# # Store in Chroma vector store
# vectorstore = Chroma.from_embeddings(
#     embeddings=embedded_docs,
#     documents=all_splits,
#     collection_name="rag-chroma"
# )

# # Use the vector store as a retriever
# retriever = vectorstore.as_retriever()

retriever = vectorstore.as_retriever(search_kwargs={"k": 3})

In [54]:
retriever

VectorStoreRetriever(tags=['Chroma', 'HuggingFaceEmbeddings'], vectorstore=<langchain_community.vectorstores.chroma.Chroma object at 0x14c041973550>, search_kwargs={'k': 3})

In [55]:
# !pip install langchain_huggingface

## LLMs

In [56]:
### Retrieval Grader

from langchain.prompts import PromptTemplate
from langchain_community.chat_models import ChatOllama
from langchain_core.output_parsers import JsonOutputParser
from langchain_mistralai.chat_models import ChatMistralAI
from langchain_core.messages import (
    HumanMessage,
    SystemMessage,
)
from langchain_huggingface import ChatHuggingFace
# LLM

from langchain_openai import ChatOpenAI


if run_local == "Yes":

#     from langchain_huggingface.llms import HuggingFacePipeline

#     hf = HuggingFacePipeline.from_model_id(
#         model_id="meta-llama/Llama-2-13b-chat-hf",
#         task="text-generation",
#         pipeline_kwargs={"max_new_tokens": 256,'temperature' :1e-10},
#         device = 0,
#     )
    llm = ChatOpenAI(
        model="gpt-3.5-turbo-0125",
        temperature=0,
        max_tokens=None,
        timeout=None,
        max_retries=2,
        api_key="",  # if you prefer to pass api key in directly instaed of using env vars
        # base_url="...",
        # organization="...",
        # other params...
    )
    # chat_model = ChatHuggingFace(llm=llm)
    chat_model = llm
else:
    llm = ChatMistralAI(
        model="mistral-medium", temperature=0, mistral_api_key=mistral_api_key
    )
    print("yesmistral")



In [57]:
from langchain_core.prompts import (
    ChatPromptTemplate,
    FewShotChatMessagePromptTemplate,
)
examples = [
    {"input": """Here is the retrieved document: 

 are packaged into the lipid-containing chylomicrons inside small intestine mucosal cells and then transported to the liver. In the liver, carotenoids are repackaged into lipoproteins, which transport them to cells. The retinoids are aptly named as their most notable function is in the retina of the eye where they aid in vision, particularly in seeing under low-light conditions. This is why night blindness is the most definitive sign of vitamin A deficiency.Vitamin A has several important functions in the body, including maintaining vision and a healthy immune system. Many of vitamin A’s functions in the body are similar to the functions of hormones (for example, vitamin A can interact with DNA, causing a change in protein function). Vitamin A assists in maintaining healthy skin and the linings and coverings of tissues; it also regulates growth and development. As an antioxidant, vitamin A protects cellular membranes, helps in maintaining glutathione levels, and influences the amount 

 
     Here is the user question: What is Vitamin A? Is this retrieved document relevant to user question? Yes or no.""", "output": "yes"},

]

In [58]:
example_prompt = ChatPromptTemplate.from_messages(
    [
        ("human", "{input}"),
        ("ai", "{output}"),
    ]
)
few_shot_prompt = FewShotChatMessagePromptTemplate(
    example_prompt=example_prompt,
    examples=examples,
)


In [59]:

from langchain_core.output_parsers import StrOutputParser
# prompt = PromptTemplate(
#     template="""You are a grader assessing relevance of a retrieved document to a user question. \n 
#     Here is the retrieved document: \n\n {document} \n\n 
#     Here is the user question: {question} \n 
#     Is this retrieved document relevant to user question? Yes or no. """,
#     input_variables=["question", "document"],
# )

# messages = [
#     SystemMessage(content="You are a grader assessing relevance of a retrieved document to a user question. Your answer should only be 'yes' or 'no'"),
#     HumanMessage(
#         content="What happens when an unstoppable force meets an immovable object?"
#     ),
# ]
prompt = ChatPromptTemplate.from_messages(
    [
        ("system", "You are a grader assessing relevance of a retrieved document to a user question. Your answer should only be 'yes' or 'no'"),
        few_shot_prompt,
        ("human", """Here is the retrieved document: \n\n {document} \n\n 
     Here is the user question: {question} \n 
     Is this retrieved document relevant to user question? Yes or no. """),
    ]
)

retrieval_grader = prompt | chat_model 
question = "what is Vitamin D?"
docs = retriever.get_relevant_documents(question)
doc_txt = docs[1].page_content
print(retrieval_grader.invoke({"question": question, "document": doc_txt}))

content='no' response_metadata={'token_usage': {'completion_tokens': 1, 'prompt_tokens': 534, 'total_tokens': 535}, 'model_name': 'gpt-3.5-turbo-0125', 'system_fingerprint': None, 'finish_reason': 'stop', 'logprobs': None} id='run-ed0b1a12-eb21-450d-87ef-d8c18b292d0a-0' usage_metadata={'input_tokens': 534, 'output_tokens': 1, 'total_tokens': 535}


In [60]:
docs

[Document(page_content='corticosteroid use, and diabetes mellitus. Nutritional or vitamin supplementation has not consistently been shown to be useful in preventing cataract formation. Pathogenesis The way in which these factors cause cataracts is unclear, although a com- mon pathway appears to be protein denaturation (e.g., by oxidative stress). Metabolic disturbance (hyperglycemia in diabetes mellitus or hyperuremia in dehydration or renal failure), toxins (e.g., smoking, alcohol), loss of anti-oxidant enzymes (e.g., superoxide dismutase), membrane disruption, reduced metabolism, failure of active transport, and loss of ionic–osmotic balance may all contribute to this process. Clinical presentations Common Change in vision—reduced acuity, contrast sensitivity, or color • appreciation, glare, monocular diplopia, or ghosting. Change in refraction—typically a myopic shift due to nuclear sclerosis. • Change in fundus view—clinicians may have difﬁ culty “looking in” • long before the pati

In [61]:
### Generate

from langchain import hub

# Prompt
prompt = hub.pull("rlm/rag-prompt")


# Post-processing
def format_docs(docs):
    return "\n\n".join(doc.page_content for doc in docs)


# Chain
rag_chain = prompt | chat_model | StrOutputParser()

# Run
generation = rag_chain.invoke({"context": docs, "question": question})
print(generation)

Vitamin D is a nutrient that helps the body absorb calcium and phosphorus, which are essential for bone health. It can be obtained through sunlight exposure, certain foods, and supplements. Deficiency in Vitamin D can lead to bone disorders like rickets or osteomalacia.


In [62]:
examples2 = [
    {"input": """Here is the initial question: \n what is Vitamin D? \n Write me an improved question only with no explanation: """, "output": "What are the key properties and benefits of vitamin D, and how does it contribute to maintaining overall health and wellness?"},

]

example_prompt2 = ChatPromptTemplate.from_messages(
    [
        ("human", "{input}"),
        ("ai", "{output}"),
    ]
)
few_shot_prompt2 = FewShotChatMessagePromptTemplate(
    example_prompt=example_prompt2,
    examples=examples2,
)

re_write_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", "You a question re-writer that converts an input question to a better version that is optimized for vectorstore retrieval. Look at the initial and formulate an improved question."),
        few_shot_prompt2,
        ("human", """Here is the initial question: \n\n {question} \n\n 
     Write me an improved question only with no explanation:  """),
        
    ]
)

question = "what is love?"
# re_write_prompt = PromptTemplate(
#     template="""You a question re-writer that converts an input question to a better version that is optimized \n 
#      for vectorstore retrieval. Look at the initial and formulate an improved question. \n
#      Here is the initial question: \n\n {question}. Improved question with no explanation: \n """,
#     input_variables=["generation", "question"],
# )

question_rewriter = re_write_prompt | chat_model | StrOutputParser()
question_rewriter.invoke({"question": question})

'What are the fundamental aspects and significance of love in human relationships and emotional well-being?'

# Translator

In [63]:
# 

translate_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", "You are a multilingual medical question translator, if the input question is in english, directly return the question. If it is in Portuguese/Spanish/Filipino, directly return the question translated in English."),
        ("human", """Here is the initial question: \n\n {question} \n\n 
     If not in English, return the question in English ONLY:  """),   
    ]
)

question = """"
什么是视网膜？ A 眼球 B 视网膜 C 视神经 D不知道"""


question_translator = translate_prompt | chat_model | StrOutputParser()
question_translator.invoke({"question": question})

"What is the retina? A eyeball B retina C optic nerve D don't know"

## Web Search Tool

In [64]:
### Search

from langchain_community.tools.tavily_search import TavilySearchResults

web_search_tool = TavilySearchResults(k=3)

# generateor

In [65]:

gen_prompt =ChatPromptTemplate.from_messages([ "human", "{question}"])
genner = gen_prompt | chat_model | StrOutputParser()
genner.invoke({"question": question})

'B 视网膜。视网膜是眼睛内部的一层组织，位于眼球的后部，包含了感光细胞，负责接收光线并将其转化为神经信号，然后通过视神经传送到大脑，使我们能够看到周围的世界。'

# Graph 

Capture the flow in as a graph.

## Graph state

In [66]:
from typing import List

from typing_extensions import TypedDict


class GraphState(TypedDict):
    """
    Represents the state of our graph.

    Attributes:
        question: question
        generation: LLM generation
        web_search: whether to add search
        documents: list of documents
    """

    question: str
    generation: str
    web_search: str
    documents: List[str]

In [67]:
from langchain.schema import Document


def translate(state):
    """
    Translate to english
    """
    print("---Translate---")
    question = state["question"]

    # Retrieval
    question = question_translator.invoke({"question": question})
    return {"question": question}


def retrieve(state):
    """
    Retrieve documents

    Args:
        state (dict): The current graph state

    Returns:ß
        state (dict): New key added to state, documents, that contains retrieved documents
    """
    print("---RETRIEVE---")
    question = state["question"]

    # Retrieval
    documents = retriever.get_relevant_documents(question)
    return {"documents": documents, "question": question}


def generate(state):
    """
    Generate answer

    Args:
        state (dict): The current graph state

    Returns:
        state (dict): New key added to state, generation, that contains LLM generation
    """
    print("---GENERATE---")
    question = state["question"]
    documents = state["documents"]

    # RAG generation
    generation = rag_chain.invoke({"context": documents, "question": question})
    return {"documents": documents, "question": question, "generation": generation}


def grade_documents(state):
    """
    Determines whether the retrieved documents are relevant to the question.

    Args:
        state (dict): The current graph state

    Returns:
        state (dict): Updates documents key with only filtered relevant documents
    """

    print("---CHECK DOCUMENT RELEVANCE TO QUESTION---")
    question = state["question"]
    documents = state["documents"]

    # Score each doc
    filtered_docs = []
    web_search = "No"
    for d in documents:
        score = retrieval_grader.invoke(
            {"question": question, "document": d.page_content}
        )
        print("SC", score)
        grade = score.content
        if grade == "yes":
            print("---GRADE: DOCUMENT RELEVANT---")
            filtered_docs.append(d)
        else:
            print("---GRADE: DOCUMENT NOT RELEVANT---")
            web_search = "Yes"
            continue
    return {"documents": filtered_docs, "question": question, "web_search": web_search}


def transform_query(state):
    """
    Transform the query to produce a better question.

    Args:
        state (dict): The current graph state

    Returns:
        state (dict): Updates question key with a re-phrased question
    """

    print("---TRANSFORM QUERY---")
    question = state["question"]
    documents = state["documents"]

    # Re-write question
    # better_question = question_rewriter.invoke({"question": question})
    return {"documents": documents, "question": question}


def web_search(state):
    """
    Web search based on the re-phrased question.

    Args:
        state (dict): The current graph state

    Returns:
        state (dict): Updates documents key with appended web results
    """

    print("---WEB SEARCH---")
    question = state["question"]
    documents = state["documents"]
    print("WEB SEARCH", question)
    # Web search
    docs = web_search_tool.invoke({"query":  question[:100]})

    web_results = "\n".join([d["content"] for d in docs])

    web_results = Document(page_content=web_results)
    documents.append(web_results)

    return {"documents": documents, "question": question}


### Edges


def decide_to_generate(state):
    """
    Determines whether to generate an answer, or re-generate a question.

    Args:
        state (dict): The current graph state

    Returns:
        str: Binary decision for next node to call
    """

    print("---ASSESS GRADED DOCUMENTS---")
    state["question"]
    web_search = state["web_search"]
    state["documents"]

    if web_search == "Yes":
        # All documents have been filtered check_relevance
        # We will re-generate a new query
        print(
            "---DECISION: ALL DOCUMENTS ARE NOT RELEVANT TO QUESTION, TRANSFORM QUERY---"
        )
        return "transform_query"
    else:
        # We have relevant documents, so generate answer
        print("---DECISION: GENERATE---")
        return "generate"

## Build Graph

This just follows the flow we outlined in the figure above.

In [68]:
from langgraph.graph import END, StateGraph

workflow = StateGraph(GraphState)

# Define the nodes
workflow.add_node("translate", translate)
workflow.add_node("generate", generate)  # generatae

# Build graph
workflow.set_entry_point("translate")
workflow.add_edge("translate","generate")
workflow.add_edge("generate", END)

# Compile
app = workflow.compile()

In [71]:
import numpy as np
import pandas as pd
from tqdm.notebook import tqdm
import csv

# Load dataset
QA = pd.read_csv('')
q_eng = QA['english'].copy()

# Function to generate answers
def generate_answers(questions):
    results = []
    for q_e in tqdm(questions): 
        inputs = {"question": "You are an expert medical assistant.\
You will be provided with medical queries, answer only in a,b,c,d:" + q_e}
        for output in app.stream(inputs):
            for key, value in output.items():
                pass
        results.append(value["generation"])
    return results

# Initial generation
results_eng = generate_answers(q_eng)

# Open the file in write mode
file_name = 'en3.5t2.csv'
with open(file_name, mode='w', newline='') as file:
    writer = csv.writer(file)
    for item in results_eng:
        writer.writerow([item]) 

# Function to check if answers are valid
def are_valid_answers(answers):
    valid_answers = {'a', 'b', 'c', 'd'}
    return [answer[0] in valid_answers for answer in answers]

# Iteratively generate answers until all are valid or patience level is reached
iteration = 0
patience = 10
valid_flags = are_valid_answers(results_eng)

while not all(valid_flags) and iteration < patience:
    iteration += 1
    num_valid = sum(valid_flags)
    num_invalid = len(valid_flags) - num_valid
    print(f"Iteration {iteration}: {num_valid} valid answers, {num_invalid} invalid answers")
    
    # Find indexes of invalid answers
    invalid_indexes = [index for index, is_valid in enumerate(valid_flags) if not is_valid]
    
    # Generate new answers for invalid questions
    invalid_questions = [q_eng[index] for index in invalid_indexes]
    new_answers = generate_answers(invalid_questions)
    
    # Update results with new answers
    for i, index in enumerate(invalid_indexes):
        results_eng[index] = new_answers[i]
    
    # Re-check validity of all answers
    valid_flags = are_valid_answers(results_eng)

# Final status
if all(valid_flags):
    print("All answers are now valid.")
else:
    print("Reached patience limit. Some answers are still invalid.")

# Final comparison with ground truth
res = pd.DataFrame(results_eng, columns=['answer'])
gt = QA.answer.str.lower().tolist()
preds = res['answer'].str[0].tolist()  # Take only the first character
first_chars = [s[0] for s in preds if s]  # Ensure the string is not empty

print(first_chars)
print((np.array(first_chars) == np.array(gt)).sum())

# Save final results to CSV
file_name_final = 'en_3.5t2.csv'
with open(file_name_final, mode='w', newline='') as file:
    writer = csv.writer(file)
    for item in results_eng:
        writer.writerow([item])


In [70]:
import numpy as np
import pandas as pd
from tqdm.notebook import tqdm
import csv

# Open the file in write mode
file_name = 'en3.5t2.csv'
with open(file_name, mode='w', newline='') as file:
    writer = csv.writer(file)
    for item in results_eng:
        writer.writerow([item]) 

# Function to check if answers are valid
def are_valid_answers(answers):
    valid_answers = {'a', 'b', 'c', 'd'}
    return [answer[0] in valid_answers for answer in answers]

# Iteratively generate answers until all are valid or patience level is reached
iteration = 0
patience = 10
valid_flags = are_valid_answers(results_eng)

while not all(valid_flags) and iteration < patience:
    iteration += 1
    num_valid = sum(valid_flags)
    num_invalid = len(valid_flags) - num_valid
    print(f"Iteration {iteration}: {num_valid} valid answers, {num_invalid} invalid answers")
    
    # Find indexes of invalid answers
    invalid_indexes = [index for index, is_valid in enumerate(valid_flags) if not is_valid]
    
    # Generate new answers for invalid questions
    invalid_questions = [q_eng[index] for index in invalid_indexes]
    new_answers = generate_answers(invalid_questions)
    
    # Update results with new answers
    for i, index in enumerate(invalid_indexes):
        results_eng[index] = new_answers[i]
    
    # Re-check validity of all answers
    valid_flags = are_valid_answers(results_eng)

# Final status
if all(valid_flags):
    print("All answers are now valid.")
else:
    print("Reached patience limit. Some answers are still invalid.")

# Final comparison with ground truth
res = pd.DataFrame(results_eng, columns=['answer'])
gt = QA.answer.str.lower().tolist()
preds = res['answer'].str[0].tolist()  # Take only the first character
first_chars = [s[0] for s in preds if s]  # Ensure the string is not empty

print(first_chars)
print((np.array(first_chars) == np.array(gt)).sum())

# Save final results to CSV
file_name_final = 'en_3.5t2.csv'
with open(file_name_final, mode='w', newline='') as file:
    writer = csv.writer(file)
    for item in results_eng:
        writer.writerow([item])


In [77]:
import numpy as np
import pandas as pd
from langchain import hub
from langchain.prompts import PromptTemplate
from tqdm.notebook import tqdm
import csv
import json

# Define the generate_prompt function
def generate_prompt(LANGUAGES, REASONING, Responses=['A', 'B', 'C', 'D']):
    delimiter = "####"
    languages_text = ", ".join(LANGUAGES)
    responses_text = ", ".join(Responses)

    system_message = f"""You are an expert medical assistant.\
    You will be provided with medical queries in these languages: {languages_text}. \
    Answer the question as best as possible."""

    template = system_message + "\n{format_instructions}\n{question}"

    response_schema = {
        "name": "response",
        "description": f"This is the option of the correct response. Could be only any of these: {responses_text}"
    }

    if REASONING:
        reasoning_schema = {
            "name": "reasoning",
            "description": "This is the reasons for the answer"
        }
        response_schemas = [response_schema, reasoning_schema]
    else:
        response_schemas = [response_schema]

    format_instructions = "Respond with a JSON object containing the following keys:\n" + \
                          "\n".join([f"{schema['name']}: {schema['description']}" for schema in response_schemas])

    prompt = PromptTemplate(
        template=template,
        input_variables=["question"],
        partial_variables={"format_instructions": format_instructions}
    )
    
    return prompt

# Custom parsing function
def parse_response(response_text):
    try:
        response_json = json.loads(response_text)
        return response_json.get("response", "invalid")
    except json.JSONDecodeError:
        return "invalid"

# Load dataset
QA = pd.read_csv('')
q_eng = QA['english'].copy()

# Generate prompt
LANGUAGES = ["English"]
REASONING = False
prompt = generate_prompt(LANGUAGES, REASONING)

# Post-processing function (from your current generation)
def format_docs(docs):
    return "\n\n".join(doc.page_content for doc in docs)

# Define the generation function using LangChain
def generate_answers(questions):
    results = []
    for q_e in tqdm(questions): 
        formatted_prompt = prompt.format(question=q_e)
        inputs = {"question": formatted_prompt}
        generation = rag_chain.invoke({"context": [], "question": inputs["question"]})
        print(generation)  # Print the generation to understand its structure
        parsed_response = parse_response(generation)
        results.append(parsed_response)
    return results

# Initial generation
results_eng = generate_answers(q_eng)

# Open the file in write mode
file_name = 'output3.5.csv'
with open(file_name, mode='w', newline='') as file:
    writer = csv.writer(file)
    for item in results_eng:
        writer.writerow([item]) 

# Function to check if answers are valid
def are_valid_answers(answers):
    valid_answers = {'a', 'b', 'c', 'd','A','B','C','D'}
    return [answer[0] in valid_answers for answer in answers]

# Iteratively generate answers until all are valid or patience level is reached
iteration = 0
patience = 10
valid_flags = are_valid_answers(results_eng)

while not all(valid_flags) and iteration < patience:
    iteration += 1
    num_valid = sum(valid_flags)
    num_invalid = len(valid_flags) - num_valid
    print(f"Iteration {iteration}: {num_valid} valid answers, {num_invalid} invalid answers")
    
    # Find indexes of invalid answers
    invalid_indexes = [index for index, is_valid in enumerate(valid_flags) if not is_valid]
    
    # Generate new answers for invalid questions
    invalid_questions = [q_eng[index] for index in invalid_indexes]
    new_answers = generate_answers(invalid_questions)
    
    # Update results with new answers
    for i, index in enumerate(invalid_indexes):
        results_eng[index] = new_answers[i]
    
    # Re-check validity of all answers
    valid_flags = are_valid_answers(results_eng)

# Final status
if all(valid_flags):
    print("All answers are now valid.")
else:
    print("Reached patience limit. Some answers are still invalid.")




In [1]:
# Final comparison with ground truth
res = pd.DataFrame(results_eng, columns=['answer'])
gt = QA.answer.str.lower().tolist()
preds = res['answer'].str[0].tolist()  # Take only the first character
first_chars = [s[0].lower() for s in preds if s]  # Ensure the string is not empty

print(first_chars)
print((np.array(first_chars) == np.array(gt)).sum())

# Save final results to CSV
file_name_final = 'final_output.csv'
with open(file_name_final, mode='w', newline='') as file:
    writer = csv.writer(file)
    for item in results_eng:
        writer.writerow([item])